均线 一

我是格子衫小C（微信公众号：格子衫小C），今天开始，我们一起来研究均线指标（Indicator）。

均线是最常见的一种指标，一般交易软件里都能看到。

均线，顾名思义，就是用各种加权算法算出历史平均价格。

因为均线有明显的滞后性（譬如用前5日价格算出来的平均数，高点或低点都一定是滞后的），所以一般叫 移动平均线，也就是 Moving Averages ，简称 MA。

MA里，平均数的算法有很多种，因此MA也有很多种，其中，最简单的就是算术平均数算出来的，一般叫 MA 或 SMA。

In [1]:
import pandas as pd
from datetime import datetime
import trdb2py

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

In [12]:
# 具体基金
# asset = 'jrj.510310'
asset = 'jqdata.000300_XSHG|1d'

# 起始时间，0表示从最开始算起
# tsStart = 0
tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
# tsEnd = -1
tsEnd = int(trdb2py.str2timestamp('2020-09-30', '%Y-%m-%d'))

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

In [13]:
# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='baseline',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaseline, toImg=isStaticImg, width=width, height=height)

我们还是拿沪深300指数，2013年5月1日到2020年9月30日的日线数据来做例子。

In [4]:
ret = trdb2py.getAssetCandles2(trdb2cfg, asset, tsStart, tsEnd, indicators=['sma.2', 'sma.5', 'sma.30', 'sma.60', 'sma.120', 'sma.240'])
# print(ret) 
# ret
trdb2py.showAssetCandles2('沪深300指数', ret, indicators=['sma.2', 'sma.5', 'sma.30', 'sma.60', 'sma.120', 'sma.240'], toImg=isStaticImg, width=width, height=height)

上面可以看到30日、60日、120日、240日均线，可以看到，随着容纳的数据变多，均线是越来越平滑的。

1. 越大的均线越平滑
2. 越大的均线高点越低，低点越高
3. 越长的均线滞后性越明显

将均线和价格曲线对比来看，我们能发现

1. 上涨时，价格曲线在均线上方（均线的滞后性）
2. 下跌时，价格曲线在下方

看起来，只要找到一条合适的均线，在价格向上穿过均线时买入，价格向下穿过均线时卖出，但其实没这么简单。

越长的均线相交点越少，但滞后越严重，而越短的均线，很容易有误穿的情况。

而且，理论上，这个均线参数不会适用所有情况，哪怕是一种资产的均线。

接下来，测一下均线

In [18]:
lstparams = []

for ema in range(61, 241):    
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['upcross'],
        strVals=['ta-sma.{}'.format(ema)],
    )
    
    buy1 = trdb2py.trading2_pb2.CtrlCondition(
        name='waittostart',
        vals=[ema],
    )    
            
    sell0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['downcross'],
        strVals=['ta-sma.{}'.format(ema)],
    )
    
    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )

    s0.buy.extend([buy0, buy1])
    s0.sell.extend([sell0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell) 
    s0.paramsInit.CopyFrom(paramsinit)        
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='sma.{}'.format(ema),
    ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=2.3)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [17]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

# dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 2]

dfpnl[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
8    sma.135     0.302877       2015-06-08     2016-08-01      2.526526   
7    sma.134     0.302877       2015-06-08     2016-08-01      2.464083   
6    sma.133     0.302266       2015-06-08     2016-08-01      2.416803   
9    sma.136     0.334525       2015-06-08     2016-08-01      2.405653   
10   sma.137     0.336601       2015-06-08     2016-08-01      2.398148   
2     sma.42     0.205037       2019-04-19     2020-05-22      2.377462   
0     sma.35     0.258460       2015-06-08     2016-06-27      2.359716   
4    sma.120     0.291283       2015-06-08     2016-06-29      2.344876   
11   sma.141     0.340096       2015-06-08     2016-08-01      2.333954   
3    sma.119     0.291283       2015-06-08     2016-06-28      2.323125   
5    sma.121     0.291283       2015-06-08     2016-06-29      2.321375   
1     sma.41     0.213162       2017-11-22     2019-01-23      2.308137   
12   sma.166     0.356306       2015-06-08     2016-09-26      2.301039   
13     sma.2     0.338487       2015-06-08     2016-03-01      2.295215   
14   sma.168     0.358394       2015-06-08     2016-09-26      2.293575   
15   sma.140     0.358305       2015-06-08     2016-08-01      2.290203   
16    sma.37     0.207975       2017-11-22     2019-01-17      2.285312   
17    sma.46     0.205666       2017-11-22     2019-01-23      2.272987   
18    sma.34     0.269154       2015-06-08     2016-06-27      2.272639   
19   sma.142     0.365292       2015-06-08     2016-08-01      2.269013   
20   sma.143     0.365292       2015-06-08     2016-08-01      2.269013   
21   sma.167     0.366182       2015-06-08     2016-09-26      2.265734   
22    sma.44     0.196864       2017-11-22     2019-01-23      2.261923   
25   sma.236     0.343879       2015-06-08     2016-12-29      1.921117   
26   sma.237     0.343879       2015-06-08     2016-12-29      1.921117   
27   sma.238     0.343879       2015-06-08     2016-12-29      1.921117   
28   sma.239     0.343879       2015-06-08     2016-12-29      1.910182   
30  baseline     0.466961       2015-06-08     2016-01-28      1.874480   
23   sma.234     0.363057       2015-06-08     2016-12-29      1.862814   
24   sma.235     0.363057       2015-06-08     2016-12-29      1.843251   
29   sma.240     0.366678       2015-06-08     2016-12-29      1.827910   

      sharpe  annualizedReturns  annualizedVolatility  variance  
8   1.124235           0.205786              0.156360  0.224423  
7   1.071079           0.197368              0.156261  0.210389  
6   1.030181           0.190994              0.156278  0.198287  
9   1.011514           0.189491              0.157676  0.189818  
10  1.005086           0.188480              0.157678  0.187792  
2   1.034221           0.185691              0.150539  0.210880  
0   1.006630           0.183299              0.152289  0.177686  
4   0.960273           0.181298              0.157557  0.202396  
11  0.929030           0.179826              0.161271  0.180135  
3   0.941141           0.178366              0.157645  0.198906  
5   0.939883           0.178130              0.157605  0.196240  
1   0.974971           0.176346              0.150102  0.182823  
12  0.872791           0.175389              0.166579  0.158424  
13  0.895708           0.174604              0.161440  0.117634  
14  0.866620           0.174382              0.166604  0.156980  
15  0.894078           0.173928              0.160979  0.166603  
16  0.948807           0.173269              0.150999  0.178809  
17  0.924363           0.171607              0.153194  0.168356  
18  0.929693           0.171560              0.152265  0.163669  
19  0.870488           0.171071              0.162060  0.160915  
20  0.870488           0.171071              0.162060  0.160915  
21  0.843888           0.170629              0.166645  0.150210  
22  0.914687           0.170116              0.153184  0.167847  
25  0.543342          

可以看到，简单的均线策略，最好的情况也就是将上涨的趋势把握住，跳过下跌大的区间，当然，基本上上涨和下跌都会有损失。

这里粒度非常重要，看估计很难看出来，只能试。

In [19]:
# lstems = [2, 42, 60]
# 起始时间，0表示从最开始算起
tsStart = 0
# tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
tsEnd = -1
# tsEnd = int(trdb2py.str2timestamp('2020-09-30', '%Y-%m-%d'))

# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='baseline',
)  

pnlBaselineF = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaselineF, toImg=isStaticImg, width=width, height=height)

In [20]:
lstparams = []

lstems = [2, 35, 42, 60, 135, 197, 240]
# 起始时间，0表示从最开始算起
tsStart = 0
# tsStart = int(trdb2py.str2timestamp('2013-05-01', '%Y-%m-%d'))

# 结束时间，-1表示到现在为止
tsEnd = -1
# tsEnd = int(trdb2py.str2timestamp('2020-09-30', '%Y-%m-%d'))

for ema in lstems:    
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['upcross'],
        strVals=['ta-sma.{}'.format(ema)],
    )
    
    buy1 = trdb2py.trading2_pb2.CtrlCondition(
        name='waittostart',
        vals=[ema],
    )    
            
    sell0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['downcross'],
        strVals=['ta-sma.{}'.format(ema)],
    )
    
    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )

    s0.buy.extend([buy0, buy1])
    s0.sell.extend([sell0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell) 
    s0.paramsInit.CopyFrom(paramsinit)        
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='sma.{}'.format(ema),
    ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=2.3)

trdb2py.showPNLs(lstpnlmix + [pnlBaselineF], toImg=isStaticImg, width=width, height=height)

In [21]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaselineF])

# dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 2]

dfpnl[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
1    sma.42     0.317224       2008-01-14     2009-01-15     18.853304   
3   sma.135     0.378201       2009-08-03     2014-07-22     14.226703   
6    sma.35     0.276939       2008-01-14     2008-11-28     14.077395   
4   sma.197     0.358136       2009-08-03     2014-07-25     12.492496   
2    sma.60     0.411195       2009-08-03     2012-12-13     11.943425   
5   sma.240     0.386300       2009-08-03     2014-08-28      8.574028   
7  baseline     0.723038       2007-10-16     2008-11-04      5.131249   
0     sma.2     0.424350       2008-01-14     2008-11-07      4.653762   

     sharpe  annualizedReturns  annualizedVolatility   variance  
1  6.173806           1.115831              0.175877  28.218082  
3  4.323498           0.826669              0.184265  11.027161  
6  4.450345           0.817337              0.176916  13.685123  
4  3.649908           0.718281              0.188575   8.780359  
2  3.683646           0.683964              0.177532  11.890634  
5  2.315743           0.473377              0.191462   3.747662  
7  0.856241           0.258269              0.266595   1.128936  
0  1.051189           0.228360              0.188701   0.921770